In [1]:
!git clone https://github.com/RafaelDaddio/BigDataAulasPUC.git

fatal: destination path 'BigDataAulasPUC' already exists and is not an empty directory.


In [2]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://archive.apache.org/dist/spark/spark-3.2.0/spark-3.2.0-bin-hadoop3.2.tgz -O spark-3.2.0-bin-hadoop3.2.tgz
!tar xf spark-3.2.0-bin-hadoop3.2.tgz
!pip install -q findspark
!pip install -q pyspark

E: Failed to fetch http://security.ubuntu.com/ubuntu/pool/universe/o/openjdk-8/openjdk-8-jre-headless_8u292-b10-0ubuntu1~18.04_amd64.deb  404  Not Found [IP: 91.189.88.152 80]
E: Failed to fetch http://security.ubuntu.com/ubuntu/pool/universe/o/openjdk-8/openjdk-8-jdk-headless_8u292-b10-0ubuntu1~18.04_amd64.deb  404  Not Found [IP: 91.189.88.152 80]
E: Unable to fetch some archives, maybe run apt-get update or try with --fix-missing?


In [3]:
import os

import findspark
findspark.init('spark-3.2.0-bin-hadoop3.2')

import pyspark
import random

sc = pyspark.SparkContext(appName='Tarefa_02')

In [4]:
# Carregando os datasets
flights_file = '/content/BigDataAulasPUC/Datasets/Flights_old/flights.csv'
flights_RDD = sc.textFile(flights_file)

num_lines_flights = sum(1 for line in open(flights_file))

#Exercicio 01

In [5]:
print(flights_RDD.take(5))

['2014-04-01,19805,1,JFK,LAX,0854,-6.00,1217,2.00,355.00,2475.00', '2014-04-01,19805,2,LAX,JFK,0944,14.00,1736,-29.00,269.00,2475.00', '2014-04-01,19805,3,JFK,LAX,1224,-6.00,1614,39.00,371.00,2475.00', '2014-04-01,19805,4,LAX,JFK,1240,25.00,2028,-27.00,264.00,2475.00', '2014-04-01,19805,5,DFW,HNL,1300,-5.00,1650,15.00,510.00,3784.00']


##a) O tempo total de voo de cada compania

In [6]:
def read_line_time(line):
    record = line.split(',')
    return (record[1],float(record[9]))

time_RDD = flights_RDD.map(read_line_time)
print(time_RDD.reduceByKey(lambda a,b: a+b).take(100))

[('19930', 2001295.0), ('20409', 3009096.0), ('20366', 4142864.0), ('20437', 799733.0), ('19690', 449242.0), ('20355', 4194811.0), ('21171', 916098.0), ('19805', 6273366.0), ('19790', 7747256.0), ('20436', 689589.0), ('20398', 2391168.0), ('20304', 3625141.0), ('19977', 6757883.0), ('19393', 9959718.0)]


##b) Qual o destino mais visado

In [7]:
def read_line_destiny(line):
    record = line.split(',')
    return (record[4],1)

destiny_RDD = flights_RDD.map(read_line_destiny).countByKey()
max_key = max(destiny_RDD, key=destiny_RDD.get)
print(str(max_key)+': '+str(destiny_RDD[max_key]))

ATL: 30953


##c) Quais aeroportos cada compania passou

In [8]:
def read_line_airports_origin(line):
  record = line.split(',')
  return (record[1],record[3])

def read_line_airports_destiny(line):
  record = line.split(',')
  return (record[1], record[4])

airports_RDD_origin = flights_RDD.map(read_line_airports_origin)
airports_RDD_destiny = flights_RDD.map(read_line_airports_destiny)

airports_RDD = airports_RDD_origin.union(airports_RDD_destiny).groupByKey()

#Aqui peguei só 5 pois estava dando IOPub data rate exceeded

for comp, airports in airports_RDD.take(5):
  print(comp, sorted(list(airports)))

19930 ['ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADK', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ADQ', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC', 'ANC',

##d) O vôo de maior distância de cada companhia

In [9]:
def read_line_airports_distance(line):
  record = line.split(',')
  return (record[1], float(record[10]))

distance_RDD = flights_RDD.map(read_line_airports_distance).groupByKey()

for comp, distances in distance_RDD.take(100):
  print(comp, max(list(distances)))

19930 2874.0
20409 2704.0
20366 1389.0
20437 2139.0
19690 4983.0
20355 2979.0
21171 2704.0
19805 3784.0
19790 4502.0
20436 1703.0
20398 1379.0
20304 1535.0
19977 4962.0
19393 2335.0


##e) Qual é o vôo mais frequente de cada companhia

In [10]:
def read_line_freq(line):
  record = line.split(',')
  return (record[1], int(record[2]))

freq_RDD = flights_RDD.map(read_line_freq).groupByKey()

#Aqui peguei só 10 pois estava demorando muito para rodar

for comp, freq in freq_RDD.take(10):
  freq_list = list(freq)
  print(comp, max(freq_list, key=freq_list.count))

19930 64
20409 2054
20366 2514
20437 221
19690 1
20355 409
21171 251
19805 29
19790 1258
20436 143


#Exercicio 02
Utilizando o dataset shakespeare.txt, faça uma operação de MapReduce para construir um índice invertido contendo como chave uma palavra e como valor uma lista de linhas onde ela foi mencionada.

In [11]:
shakespeare_file = '/content/BigDataAulasPUC/Datasets/shakespeare.txt'
shakespeare_RDD = sc.textFile(shakespeare_file)

num_lines_shakespeare = sum(1 for line in open(shakespeare_file))

In [12]:
print(shakespeare_RDD.take(5))

['hamlet@0\t\tHAMLET', 'hamlet@8\t', 'hamlet@9\t', 'hamlet@10\t\tDRAMATIS PERSONAE', 'hamlet@29\t']


In [13]:
def read_line_shake(line):
    split = line.split('\t', 1)
    words = split[1].strip().replace('\t', ' ').split()
    for word in words:
        yield word, split[0]

words_RDD = shakespeare_RDD.flatMap(read_line_shake).groupByKey()

for word, lines in words_RDD.collect():
    print(word, list(lines))

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



bears ['hamlet@14414', 'kingrichardiii@66155', 'kingrichardiii@133855', 'coriolanus@72487', 'coriolanus@135256', 'coriolanus@135844', 'troilusandcressida@29180', 'antonyandcleopatra@62734', '2kinghenryiv@3912', '2kinghenryiv@92537', 'kinglear@59278', 'kinglear@81123', 'othello@24664', 'othello@24664', 'othello@24761', 'kinghenryv@77365', 'kinghenryv@78720', '2kinghenryvi@17004', '2kinghenryvi@22852', '2kinghenryvi@34641', '2kinghenryvi@50447', '2kinghenryvi@59552', '2kinghenryvi@60315', '2kinghenryvi@143454', 'kinghenryviii@28209', 'kinghenryviii@96424', 'kinghenryviii@104712', '3kinghenryvi@27816', '3kinghenryvi@47421', '3kinghenryvi@78858', 'winterstale@20568', '1kinghenryiv@28382', '1kinghenryiv@40328', '1kinghenryiv@76637', '1kinghenryiv@107756', '1kinghenryiv@138934', 'romeoandjuliet@31478', 'kingrichardii@28862', '1kinghenryvi@44464', '1kinghenryvi@47993', '1kinghenryvi@102158', 'merrywivesofwindsor@13138', 'merrywivesofwindsor@17756', 'measureforemeasure@54590', 'measureforemeas

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
grave-stone ['timonofathens@88902', 'timonofathens@106806', 'timonofathens@112231']
sire! ['timonofathens@89053']
solder'st ['timonofathens@89285']
throng'd ['timonofathens@89624', 'periclesprinceoftyre@7386', 'periclesprinceoftyre@29029', 'rapeoflucrece@65225']
Throng'd ['timonofathens@89660']
Moe ['timonofathens@89830', 'timonofathens@91476']
Banditti] ['timonofathens@89881', 'timonofathens@92653']
Bandit ['timonofathens@89900', 'timonofathens@90103', 'timonofathens@90159', 'timonofathens@90304', 'timonofathens@90366', 'timonofathens@90413', 'timonofathens@90450', 'timonofathens@90949', 'timonofathens@92293', 'timonofathens@92374', 'timonofathens@92482', 'timonofathens@92551']
fragment, ['timonofathens@89961']
Banditti ['timonofathens@90396', 'timonofathens@90480', 'timonofathens@90529', 'timonofathens@90597']
roots; ['timonofathens@90706']
berries, ['timonofathens@90949']
shapes: ['timonofathens@91195']
Rascal ['timonofathen

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
goblins ['hamlet@164361', 'troilusandcressida@157562', 'tempest@82403']
supervise, ['hamlet@164406']
leisure ['hamlet@164406', 'kingrichardiii@13855', 'kingrichardiii@41613', 'kingrichardiii@143216', 'kingrichardiii@164514', 'kingrichardiii@164691', 'kingrichardiii@171964', 'troilusandcressida@102382', 'troilusandcressida@125603', 'antonyandcleopatra@17030', '2kinghenryiv@118086', 'kinglear@60477', 'kinghenryviii@85916', '1kinghenryiv@102743', 'romeoandjuliet@106192', 'allswellthatendswell@134891', 'kingrichardii@1532', 'kingrichardii@30987', '1kinghenryvi@7699', 'measureforemeasure@15480', 'measureforemeasure@77243', 'measureforemeasure@124120', 'tamingoftheshrew@32047', 'tamingoftheshrew@58839', 'muchadoaboutnothing@59602', 'merchantofvenice@104810', 'kingjohn@16805', 'kingjohn@116109', 'macbeth@48528', 'tempest@95067', 'sonnets@24348', 'sonnets@27643', 'sonnets@74370', 'comedyoferrors@50979', 'comedyoferrors@86793', 'rapeofl

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
stay'd! ['macbeth@8311']
insane ['macbeth@8412']
Cawdor: ['macbeth@9365', 'macbeth@10773']
thane! ['macbeth@9415']
robes? ['macbeth@9592']
capital, ['macbeth@9903']
oftentimes, ['macbeth@10343']
truths, ['macbeth@10383']
theme.--I ['macbeth@10602']
soliciting ['macbeth@10652']
imaginings: ['macbeth@10988']
partner's ['macbeth@11182']
MACBETH, ['macbeth@12738', 'macbeth@14897', 'macbeth@24967', 'macbeth@41974', 'macbeth@42021', 'macbeth@43583', 'macbeth@52665', 'macbeth@52665', 'macbeth@87920', 'macbeth@92291', 'macbeth@96649']
deserved, ['macbeth@12921', 'macbeth@13501']
duties; ['macbeth@13204']
enfold ['macbeth@13548']
Malcolm, ['macbeth@13866', 'macbeth@90734']
Cumberland; ['macbeth@13911']
unaccompanied ['macbeth@13956']
deservers. ['macbeth@14041']
Cumberland! ['macbeth@14313']
Banquo; ['macbeth@14612', 'macbeth@49891']
Macbeth's ['macbeth@14858', 'macbeth@18568', 'macbeth@20288', 'macbeth@24447', 'macbeth@39292']
saluted 